In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import datetime as dt
from functools import partial
import os

import warnings
warnings.filterwarnings('ignore')

import sqlalchemy
from sqlalchemy.ext.automap import automap_base
from sqlalchemy.orm import Session
from sqlalchemy import create_engine, inspect, func, and_, or_
from sqlalchemy.ext.declarative import declarative_base
from sqlalchemy import Column, Integer, String, Float

import pymysql
pymysql.install_as_MySQLdb()

# from flask import Flask, jsonify

# Creating database
import sqlite3

In [2]:
Base = declarative_base()

class Eruptions(Base):
    __tablename__ = 'eruptions'
    id = Column(Integer, primary_key=True)
    volcano_name = Column(String)
    vei = Column(Integer)
    start_year = Column(Integer)
    start_month = Column(Integer)
    start_day = Column(Integer)
    end_year = Column(Integer)
    end_month = Column(Integer)
    end_day = Column(Integer)
    country = Column(String)
    region = Column(String)
    latitude = Column(Float)
    longitude = Column(Float)
    elevation = Column(Float)
    primary_volcano_type = Column(String)
    status = Column(String)

class TempInfo(Base):
    __tablename__ = 'tempinfo'
    id = Column(Integer, primary_key=True)
    year = Column(Float)
    temp = Column(Float)
    fit = Column(Float)
    
    
class WorldCities(Base):
    __tablename__ = 'worldcities'
    id = Column(Integer, primary_key=True)
    city = Column(String)
    city_ascii = Column(String)
    lat = Column(Float)
    lng = Column(Float)
    pop = Column(Float)
    country = Column(String)
    iso2 = Column(String)
    iso3 = Column(String)
    province = Column(String)
    
class BerkeleyData(Base):
    __tablename__ = 'berkeleydata'
    id = Column(Integer, primary_key=True)
    year = Column(Float)
    log_CO2_277_3 = Column(Float)
    volcanic = Column(Float)
    temperature_C = Column(Float)
    fit = Column(Float)
    
class Risk(Base):
    __tablename__ = 'risk'
    id = Column(Integer, primary_key=True)
    city = Column(String)
    lat = Column(Float)
    lng = Column(Float)
    pop = Column(Float)
    country = Column(String)
    time = Column(Float)
    dist = Column(Float)
    risk = Column(Float)
    
engine = create_engine('sqlite:///volcano_app/volcano.sqlite')
conn = engine.connect()
conn = engine.raw_connection()
cursor = conn.cursor()
command = "DROP TABLE IF EXISTS {};".format('eruptions')
cursor.execute(command)
conn.commit()
cursor.close()

conn = engine.connect()
conn = engine.raw_connection()
cursor = conn.cursor()
command = "DROP TABLE IF EXISTS {};".format('tempinfo')
cursor.execute(command)
conn.commit()
cursor.close()

conn = engine.connect()
conn = engine.raw_connection()
cursor = conn.cursor()
command = "DROP TABLE IF EXISTS {};".format('worldcities')
cursor.execute(command)
conn.commit()
cursor.close()

conn = engine.connect()
conn = engine.raw_connection()
cursor = conn.cursor()
command = "DROP TABLE IF EXISTS {};".format('berkeleydata')
cursor.execute(command)
conn.commit()
cursor.close()

conn = engine.connect()
conn = engine.raw_connection()
cursor = conn.cursor()
command = "DROP TABLE IF EXISTS {};".format('risk_data')
cursor.execute(command)
conn.commit()
cursor.close()

conn = engine.connect()
conn = engine.raw_connection()
cursor = conn.cursor()
command = "DROP TABLE IF EXISTS {};".format('risk')
cursor.execute(command)
conn.commit()
cursor.close()

conn = engine.connect()
# Create the garbage_collection table within the database
Base.metadata.create_all(conn)

# To push the objects made and query the server we use a Session object
from sqlalchemy.orm import Session
session = Session(bind=engine)

In [3]:
# os.rename('clean_eruptions.xlsx', 'clean_eruptions1.csv') 
# erupt_df = pd.read_excel('clean_eruptions.csv', encoding = 'utf-8')
erupt_df = pd.read_excel('finalized_data/clean_eruptions.xlsx')
tempInfo_df = pd.read_csv('finalized_data/tempInfo.csv')
berkeley_df = pd.read_csv('finalized_data/berkeleydata.csv')
worldcities_df = pd.read_csv('finalized_data/simplemaps-worldcities-basic.csv')
risk_df = pd.read_csv('finalized_data/risk_data.csv')

In [4]:
risk_df.info()
risk_df.head()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 6902 entries, 0 to 6901
Data columns (total 9 columns):
Unnamed: 0    6902 non-null int64
city          6902 non-null object
lat           6902 non-null float64
lng           6902 non-null float64
pop           6902 non-null float64
country       6902 non-null object
time          6902 non-null float64
dist          6902 non-null float64
risk          6902 non-null float64
dtypes: float64(6), int64(1), object(2)
memory usage: 485.4+ KB


Unnamed: 0           city        lat        lng       pop      country  \
0           0  Qal eh-ye Now  34.983000  63.133300    2997.0  Afghanistan   
1           1    Chaghcharan  34.516701  65.250001   15000.0  Afghanistan   
2           2    Lashkar Gah  31.582998  64.360000  201546.0  Afghanistan   
3           3         Zaranj  31.112001  61.886998   49851.0  Afghanistan   
4           4     Tarin Kowt  32.633298  65.866699   10000.0  Afghanistan   

     time        dist      risk  
0   130.0  102.390317  4.169192  
1   730.0  875.594027  0.842020  
2    77.0  694.008008  1.689544  
3   226.0  161.681496  3.633294  
4  7850.0  141.597769  3.328493

In [5]:
worldcities_df.info()
worldcities_df.head()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 7322 entries, 0 to 7321
Data columns (total 9 columns):
city          7322 non-null object
city_ascii    7322 non-null object
lat           7322 non-null float64
lng           7322 non-null float64
pop           7322 non-null float64
country       7322 non-null object
iso2          7291 non-null object
iso3          7322 non-null object
province      7203 non-null object
dtypes: float64(3), object(6)
memory usage: 514.9+ KB


city   city_ascii        lat        lng       pop      country  \
0  Qal eh-ye Now    Qal eh-ye  34.983000  63.133300    2997.0  Afghanistan   
1    Chaghcharan  Chaghcharan  34.516701  65.250001   15000.0  Afghanistan   
2    Lashkar Gah  Lashkar Gah  31.582998  64.360000  201546.0  Afghanistan   
3         Zaranj       Zaranj  31.112001  61.886998   49851.0  Afghanistan   
4     Tarin Kowt   Tarin Kowt  32.633298  65.866699   10000.0  Afghanistan   

  iso2 iso3 province  
0   AF  AFG  Badghis  
1   AF  AFG     Ghor  
2   AF  AFG  Hilmand  
3   AF  AFG   Nimroz  
4   AF  AFG  Uruzgan

In [6]:
berkeley_df.info()
berkeley_df.head()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3099 entries, 0 to 3098
Data columns (total 5 columns):
Year                  3099 non-null float64
log( CO2 / 277.3 )    3099 non-null float64
Volcanic              3099 non-null float64
Temperature (C)       3099 non-null float64
Fit                   3099 non-null float64
dtypes: float64(5)
memory usage: 121.1 KB


Year  log( CO2 / 277.3 )  Volcanic  Temperature (C)       Fit
0  1753.250000           -0.002380  0.023730         8.541808  8.331117
1  1753.333333           -0.002382  0.023055         8.617839  8.331117
2  1753.416667           -0.002384  0.022398         8.437477  8.331116
3  1753.500000           -0.002387  0.021761         8.101920  8.331115
4  1753.583333           -0.002389  0.021141         8.158572  8.331114

In [7]:
erupt_df.info()
erupt_df.head()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 9839 entries, 0 to 9838
Data columns (total 15 columns):
Volcano Name            9839 non-null object
VEI                     7563 non-null float64
Start Year              9839 non-null int64
Start Month             9659 non-null float64
Start Day               9658 non-null float64
End Year                3942 non-null float64
End Month               3940 non-null float64
End Day                 3939 non-null float64
Country                 9839 non-null object
Region                  9839 non-null object
Latitude                9839 non-null float64
Longitude               9839 non-null float64
Elevation               9839 non-null int64
Primary Volcano Type    9762 non-null object
Status                  2690 non-null object
dtypes: float64(8), int64(2), object(5)
memory usage: 1.2+ MB


Volcano Name  VEI  Start Year  Start Month  Start Day  End Year  End Month  \
0       Erebus  2.0        1972         12.0       16.0    2018.0        2.0   
1       Erebus  1.0        1972          1.0        3.0       NaN        NaN   
2       Erebus  0.0        1963         11.0       16.0       NaN        NaN   
3       Erebus  2.0        1955          7.0        2.0       NaN        NaN   
4       Erebus  2.0        1947          2.0        0.0       NaN        NaN   

   End Day     Country      Region  Latitude  Longitude  Elevation  \
0      7.0  Antarctica  Antarctica    -77.53     167.17       3794   
1      NaN  Antarctica  Antarctica    -77.53     167.17       3794   
2      NaN  Antarctica  Antarctica    -77.53     167.17       3794   
3      NaN  Antarctica  Antarctica    -77.53     167.17       3794   
4      NaN  Antarctica  Antarctica    -77.53     167.17       3794   

  Primary Volcano Type      Status  
0        Stratovolcano  Historical  
1        Stratovolcano  Historical  
2        Stratovolcano  Historical  
3        Stratovolcano  Historical  
4        Stratovolcano  Historical

In [8]:
erupt_df.iloc[21]

Volcano Name                Takahe
VEI                            NaN
Start Year                   -6250
Start Month                      0
Start Day                        0
End Year                       NaN
End Month                      NaN
End Day                        NaN
Country                 Antarctica
Region                  Antarctica
Latitude                    -76.28
Longitude                  -112.08
Elevation                     3460
Primary Volcano Type        Shield
Status                    Ice Core
Name: 21, dtype: object

In [9]:
tempInfo_df.head()

Unnamed: 0         Year      temp       Fit
0           0  1753.250000  8.541808  8.331117
1           1  1753.333333  8.617839  8.331117
2           2  1753.416667  8.437477  8.331116
3           3  1753.500000  8.101920  8.331115
4           4  1753.583333  8.158572  8.331114

In [10]:
tempInfo_df = tempInfo_df.drop(["Unnamed: 0"], axis=1)
tempInfo_df.head()

Year      temp       Fit
0  1753.250000  8.541808  8.331117
1  1753.333333  8.617839  8.331117
2  1753.416667  8.437477  8.331116
3  1753.500000  8.101920  8.331115
4  1753.583333  8.158572  8.331114

In [11]:
tempInfo_df.info()
tempInfo_df.head()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3099 entries, 0 to 3098
Data columns (total 3 columns):
Year    3099 non-null float64
temp    3099 non-null float64
Fit     3099 non-null float64
dtypes: float64(3)
memory usage: 72.7 KB


Year      temp       Fit
0  1753.250000  8.541808  8.331117
1  1753.333333  8.617839  8.331117
2  1753.416667  8.437477  8.331116
3  1753.500000  8.101920  8.331115
4  1753.583333  8.158572  8.331114

In [12]:
i = 1
for index, row in risk_df.iterrows():
    risk_data = Risk(id = i,city = row['city'],lat = row['lat'],lng = row['lng'],pop = row['pop'],country = row['country'],time = row['time'],dist = row['dist'],risk = row['risk'])
    session.add(risk_data)
    i += 1
session.commit()

In [13]:
i = 1
for index, row in erupt_df.iterrows():
    eruptions = Eruptions(id = i, volcano_name = row['Volcano Name'], vei = row['VEI'], start_year = row['Start Year'], start_month = row['Start Month'], start_day = row['Start Day'], end_year = row['End Year'], end_month = row['End Month'], end_day = row['End Day'], country = row['Country'], region = row['Region'], latitude = row['Latitude'], longitude = row['Longitude'], elevation = row['Elevation'], primary_volcano_type = row['Primary Volcano Type'], status = row['Status'])
    session.add(eruptions)
    i += 1
session.commit()

In [14]:
i = 1
for index, row in tempInfo_df.iterrows():
    tempinfo = TempInfo(id = i, year = row['Year'], temp = row['temp'], fit = row['Fit'])
    session.add(tempinfo)
    i += 1
session.commit()

In [15]:
i = 1
for index, row in berkeley_df.iterrows():
    berkeleydata = BerkeleyData(id = i, year = row['Year'],log_CO2_277_3 = row['log( CO2 / 277.3 )'],volcanic = row['Volcanic'],temperature_C = row['Temperature (C)'],fit = row['Fit'])
    session.add(berkeleydata)
    i += 1
session.commit()

In [16]:
i = 1
for index, row in worldcities_df.iterrows():
    worldcities = WorldCities(id = i,city = row['city'],city_ascii = row['city_ascii'],lat = row['lat'],lng = row['lng'],pop = row['pop'],country = row['country'],iso2 = row['iso2'],iso3 = row['iso3'],province = row['province'])
    session.add(worldcities)
    i += 1
session.commit()

In [17]:
items = session.query(TempInfo)
for item in items:
    print("-"*12)
    print("id: ", item.id)
    print("year: ", item.year)   
    print("temp: ", item.temp)
    print("fit: ", item.fit)

------------
id:  1
year:  1753.25
temp:  8.541808099999999
fit:  8.3311167
------------
id:  2
year:  1753.3333329999998
temp:  8.6178389
fit:  8.3311167
------------
id:  3
year:  1753.4166670000002
temp:  8.437477099999999
fit:  8.3311157
------------
id:  4
year:  1753.5
temp:  8.101920100000001
fit:  8.3311148
------------
id:  5
year:  1753.5833329999998
temp:  8.1585722
fit:  8.331113799999999
------------
id:  6
year:  1753.6666670000002
temp:  8.028633099999999
fit:  8.3311129
------------
id:  7
year:  1753.75
temp:  7.776057700000001
fit:  8.3311119
------------
id:  8
year:  1753.8333329999998
temp:  7.9026299
fit:  8.331111
------------
id:  9
year:  1753.9166670000002
temp:  7.9884963
fit:  8.33111
------------
id:  10
year:  1754.0
temp:  8.0020781
fit:  8.331109
------------
id:  11
year:  1754.0833329999998
temp:  7.961603200000001
fit:  8.331109
------------
id:  12
year:  1754.1666670000002
temp:  7.961489200000001
fit:  8.3311081
------------
id:  13
year:  1754.25


------------
id:  225
year:  1771.9166670000002
temp:  8.539588900000002
fit:  8.3379269
------------
id:  226
year:  1772.0
temp:  8.459897
fit:  8.3382521
------------
id:  227
year:  1772.0833329999998
temp:  8.510719300000002
fit:  8.3385744
------------
id:  228
year:  1772.1666670000002
temp:  8.520874000000001
fit:  8.3388948
------------
id:  229
year:  1772.25
temp:  8.4746761
fit:  8.339209599999998
------------
id:  230
year:  1772.3333329999998
temp:  8.5395241
fit:  8.3395233
------------
id:  231
year:  1772.4166670000002
temp:  8.792593
fit:  8.3398342
------------
id:  232
year:  1772.5
temp:  8.9601221
fit:  8.3401423
------------
id:  233
year:  1772.5833329999998
temp:  8.9849815
fit:  8.340446499999999
------------
id:  234
year:  1772.6666670000002
temp:  9.0067644
fit:  8.3407497
------------
id:  235
year:  1772.75
temp:  9.135760300000001
fit:  8.3410511
------------
id:  236
year:  1772.8333329999998
temp:  9.2322493
fit:  8.341348599999998
------------
id:  23

temp:  7.724864999999999
fit:  7.8269753
------------
id:  397
year:  1786.25
temp:  7.8346658
fit:  7.8432837
------------
id:  398
year:  1786.3333329999998
temp:  7.8531957
fit:  7.859136599999999
------------
id:  399
year:  1786.4166670000002
temp:  7.5301260999999995
fit:  7.874546499999999
------------
id:  400
year:  1786.5
temp:  7.4733367
fit:  7.889528299999999
------------
id:  401
year:  1786.5833329999998
temp:  7.626767599999999
fit:  7.904092299999999
------------
id:  402
year:  1786.6666670000002
temp:  7.7443891
fit:  7.9182505999999995
------------
id:  403
year:  1786.75
temp:  7.8914752
fit:  7.932014
------------
id:  404
year:  1786.8333329999998
temp:  7.7770958
fit:  7.9453959
------------
id:  405
year:  1786.9166670000002
temp:  7.827446000000001
fit:  7.958406
------------
id:  406
year:  1787.0
temp:  7.8989997
fit:  7.971055000000001
------------
id:  407
year:  1787.0833329999998
temp:  7.8202243000000005
fit:  7.983351700000001
------------
id:  408
yea

temp:  7.6827183
fit:  8.386841800000001
------------
id:  557
year:  1799.5833329999998
temp:  7.7602844
fit:  8.388365700000001
------------
id:  558
year:  1799.6666670000002
temp:  7.9681969
fit:  8.3898497
------------
id:  559
year:  1799.75
temp:  7.926431699999999
fit:  8.3912945
------------
id:  560
year:  1799.8333329999998
temp:  8.097436
fit:  8.392704
------------
id:  561
year:  1799.9166670000002
temp:  8.1480312
fit:  8.3940754
------------
id:  562
year:  1800.0
temp:  8.1112957
fit:  8.395412400000001
------------
id:  563
year:  1800.0833329999998
temp:  8.0621586
fit:  8.3967142
------------
id:  564
year:  1800.1666670000002
temp:  8.0499668
fit:  8.3979836
------------
id:  565
year:  1800.25
temp:  7.9817257
fit:  8.3992205
------------
id:  566
year:  1800.3333329999998
temp:  7.987647999999999
fit:  8.400425
------------
id:  567
year:  1800.4166670000002
temp:  7.9698634
fit:  8.4015989
------------
id:  568
year:  1800.5
temp:  8.1906595
fit:  8.4027424
----

id:  722
year:  1813.3333329999998
temp:  7.8306909
fit:  8.231526400000002
------------
id:  723
year:  1813.4166670000002
temp:  8.1036253
fit:  8.2377253
------------
id:  724
year:  1813.5
temp:  8.250473
fit:  8.2437477
------------
id:  725
year:  1813.5833329999998
temp:  8.3032255
fit:  8.2495985
------------
id:  726
year:  1813.6666670000002
temp:  8.1850672
fit:  8.2552834
------------
id:  727
year:  1813.75
temp:  8.2959232
fit:  8.2608061
------------
id:  728
year:  1813.8333329999998
temp:  8.188784599999998
fit:  8.2661724
------------
id:  729
year:  1813.9166670000002
temp:  7.8628445000000005
fit:  8.271386099999999
------------
id:  730
year:  1814.0
temp:  7.860073599999999
fit:  8.2764511
------------
id:  731
year:  1814.0833329999998
temp:  7.7739978
fit:  8.281372099999999
------------
id:  732
year:  1814.1666670000002
temp:  7.786351700000001
fit:  8.2861528
------------
id:  733
year:  1814.25
temp:  7.6106238
fit:  8.290798200000001
------------
id:  734
y

...

temp:  8.873423599999999
fit:  8.8411074
------------
id:  2352
year:  1949.1666670000002
temp:  8.869713800000001
fit:  8.8418436
------------
id:  2353
year:  1949.25
temp:  8.8538857
fit:  8.842573199999999
------------
id:  2354
year:  1949.3333329999998
temp:  8.848258
fit:  8.8432961
------------
id:  2355
year:  1949.4166670000002
temp:  8.84377
fit:  8.844011300000002
------------
id:  2356
year:  1949.5
temp:  8.8418436
fit:  8.8447189
------------
id:  2357
year:  1949.5833329999998
temp:  8.744126300000001
fit:  8.8454227
------------
id:  2358
year:  1949.6666670000002
temp:  8.7404222
fit:  8.846119900000001
------------
id:  2359
year:  1949.75
temp:  8.7534847
fit:  8.846812199999999
------------
id:  2360
year:  1949.8333329999998
temp:  8.7338572
fit:  8.8474979
------------
id:  2361
year:  1949.9166670000002
temp:  8.7332954
fit:  8.8481808
------------
id:  2362
year:  1950.0
temp:  8.7478886
fit:  8.8488579
------------
id:  2363
year:  1950.0833329999998
temp:  8.

temp:  9.0524712
fit:  8.9523163
------------
id:  2504
year:  1961.8333329999998
temp:  9.029314999999999
fit:  8.9536676
------------
id:  2505
year:  1961.9166670000002
temp:  8.9837961
fit:  8.954175900000001
------------
id:  2506
year:  1962.0
temp:  8.9693642
fit:  8.9550934
------------
id:  2507
year:  1962.0833329999998
temp:  8.9678621
fit:  8.9562798
------------
id:  2508
year:  1962.1666670000002
temp:  8.956789
fit:  8.956997900000001
------------
id:  2509
year:  1962.25
temp:  8.9341354
fit:  8.9587107
------------
id:  2510
year:  1962.3333329999998
temp:  8.9407415
fit:  8.9587612
------------
id:  2511
year:  1962.4166670000002
temp:  8.9451923
fit:  8.959455499999999
------------
id:  2512
year:  1962.5
temp:  8.9757853
fit:  8.960253699999999
------------
id:  2513
year:  1962.5833329999998
temp:  8.9644604
fit:  8.9611931
------------
id:  2514
year:  1962.6666670000002
temp:  8.9974108
fit:  8.9618044
------------
id:  2515
year:  1962.75
temp:  8.96817680000000

------------
id:  2666
year:  1975.3333329999998
temp:  9.0328894
fit:  9.1265564
------------
id:  2667
year:  1975.4166670000002
temp:  9.0262671
fit:  9.1278191
------------
id:  2668
year:  1975.5
temp:  9.0373821
fit:  9.1291904
------------
id:  2669
year:  1975.5833329999998
temp:  9.0186157
fit:  9.1304331
------------
id:  2670
year:  1975.6666670000002
temp:  8.991257699999998
fit:  9.132076300000001
------------
id:  2671
year:  1975.75
temp:  8.8904753
fit:  9.1340179
------------
id:  2672
year:  1975.8333329999998
temp:  8.867315300000001
fit:  9.1358213
------------
id:  2673
year:  1975.9166670000002
temp:  8.802523599999999
fit:  9.136923800000002
------------
id:  2674
year:  1976.0
temp:  8.7505484
fit:  9.137785899999999
------------
id:  2675
year:  1976.0833329999998
temp:  8.726281199999999
fit:  9.133396099999999
------------
id:  2676
year:  1976.1666670000002
temp:  8.730180699999998
fit:  9.128665
------------
id:  2677
year:  1976.25
temp:  8.709549
fit:  9.

fit:  9.4091024
------------
id:  2841
year:  1989.9166670000002
temp:  9.415122
fit:  9.4110756
------------
id:  2842
year:  1990.0
temp:  9.444973
fit:  9.4126329
------------
id:  2843
year:  1990.0833329999998
temp:  9.4540586
fit:  9.4140511
------------
id:  2844
year:  1990.1666670000002
temp:  9.452569
fit:  9.415939300000002
------------
id:  2845
year:  1990.25
temp:  9.4451742
fit:  9.4177094
------------
id:  2846
year:  1990.3333329999998
temp:  9.443491
fit:  9.419507000000001
------------
id:  2847
year:  1990.4166670000002
temp:  9.508543
fit:  9.4216185
------------
id:  2848
year:  1990.5
temp:  9.5082092
fit:  9.4235277
------------
id:  2849
year:  1990.5833329999998
temp:  9.503211
fit:  9.425059300000001
------------
id:  2850
year:  1990.6666670000002
temp:  9.533055300000001
fit:  9.4262838
------------
id:  2851
year:  1990.75
temp:  9.4338408
fit:  9.428137800000002
------------
id:  2852
year:  1990.8333329999998
temp:  9.4348993
fit:  9.43085
------------
i

temp:  9.657799699999998
fit:  9.6790514
------------
id:  3000
year:  2003.1666670000002
temp:  9.6671934
fit:  9.6817541
------------
id:  3001
year:  2003.25
temp:  9.665818199999999
fit:  9.684508300000001
------------
id:  3002
year:  2003.3333329999998
temp:  9.702301
fit:  9.6873035
------------
id:  3003
year:  2003.4166670000002
temp:  9.6891088
fit:  9.689943300000001
------------
id:  3004
year:  2003.5
temp:  9.782319099999999
fit:  9.692357099999999
------------
id:  3005
year:  2003.5833329999998
temp:  9.744525
fit:  9.6946745
------------
id:  3006
year:  2003.6666670000002
temp:  9.7758694
fit:  9.6971035
------------
id:  3007
year:  2003.75
temp:  9.7986269
fit:  9.6995258
------------
id:  3008
year:  2003.8333329999998
temp:  9.8056784
fit:  9.702356300000002
------------
id:  3009
year:  2003.9166670000002
temp:  9.750380499999999
fit:  9.704647099999999
------------
id:  3010
year:  2004.0
temp:  9.736825
fit:  9.7061901
------------
id:  3011
year:  2004.0833329

In [18]:
items = session.query(BerkeleyData)
for item in items:
    print("-"*12)
    print('id: ',item.id)
    print('year: ',item.year)
    print('log_CO2_277_3: ',item.log_CO2_277_3)
    print('volcanic: ',item.volcanic)
    print('temperature_C: ',item.temperature_C)
    print('fit: ',item.fit)

------------
id:  1
year:  1753.25
log_CO2_277_3:  -0.002379651
volcanic:  0.023730281000000002
temperature_C:  8.541808099999999
fit:  8.3311167
------------
id:  2
year:  1753.3333329999998
log_CO2_277_3:  -0.0023820910000000002
volcanic:  0.023054726
temperature_C:  8.6178389
fit:  8.3311167
------------
id:  3
year:  1753.4166670000002
log_CO2_277_3:  -0.0023844829999999997
volcanic:  0.022398402
temperature_C:  8.437477099999999
fit:  8.3311157
------------
id:  4
year:  1753.5
log_CO2_277_3:  -0.0023868279999999997
volcanic:  0.021760763
temperature_C:  8.101920100000001
fit:  8.3311148
------------
id:  5
year:  1753.5833329999998
log_CO2_277_3:  -0.002389123
volcanic:  0.021141277000000003
temperature_C:  8.1585722
fit:  8.331113799999999
------------
id:  6
year:  1753.6666670000002
log_CO2_277_3:  -0.002391368
volcanic:  0.020539426
temperature_C:  8.028633099999999
fit:  8.3311129
------------
id:  7
year:  1753.75
log_CO2_277_3:  -0.002393561
volcanic:  0.019954708
temperat

id:  125
year:  1763.5833329999998
log_CO2_277_3:  -0.001970832
volcanic:  6.792646241
temperature_C:  7.7461724
fit:  8.2304201
------------
id:  126
year:  1763.6666670000002
log_CO2_277_3:  -0.001958771
volcanic:  6.5992727879999995
temperature_C:  7.9839587
fit:  8.2334023
------------
id:  127
year:  1763.75
log_CO2_277_3:  -0.001946521
volcanic:  6.411404302
temperature_C:  8.1711645
fit:  8.2363033
------------
id:  128
year:  1763.8333329999998
log_CO2_277_3:  -0.0019340820000000002
volcanic:  6.228884067
temperature_C:  8.2003489
fit:  8.2391233
------------
id:  129
year:  1763.9166670000002
log_CO2_277_3:  -0.001921454
volcanic:  6.0515598289999994
temperature_C:  8.3388815
fit:  8.2418652
------------
id:  130
year:  1764.0
log_CO2_277_3:  -0.001908634
volcanic:  5.879283667999999
temperature_C:  8.3948975
fit:  8.244531599999998
------------
id:  131
year:  1764.0833329999998
log_CO2_277_3:  -0.0018956210000000001
volcanic:  5.711911874
temperature_C:  8.4486609
fit:  8.24

year:  1773.25
log_CO2_277_3:  0.0009662189999999999
volcanic:  0.23826523800000002
temperature_C:  9.57586
fit:  8.3428116
------------
id:  242
year:  1773.3333329999998
log_CO2_277_3:  0.001007551
volcanic:  0.23148228899999998
temperature_C:  9.5461721
fit:  8.3430996
------------
id:  243
year:  1773.4166670000002
log_CO2_277_3:  0.0010492000000000001
volcanic:  0.224892438
temperature_C:  9.2927399
fit:  8.343384700000001
------------
id:  244
year:  1773.5
log_CO2_277_3:  0.001091168
volcanic:  0.218490187
temperature_C:  9.2299051
fit:  8.343668899999999
------------
id:  245
year:  1773.5833329999998
log_CO2_277_3:  0.001133455
volcanic:  0.212270195
temperature_C:  9.027566
fit:  8.3439522
------------
id:  246
year:  1773.6666670000002
log_CO2_277_3:  0.001176063
volcanic:  0.206227275
temperature_C:  9.192032800000002
fit:  8.3442345
------------
id:  247
year:  1773.75
log_CO2_277_3:  0.001218992
volcanic:  0.200356384
temperature_C:  9.24189
fit:  8.3445148
------------
i

id:  357
year:  1782.9166670000002
log_CO2_277_3:  0.007646722
volcanic:  0.008357615
temperature_C:  8.0647011
fit:  8.3761311
------------
id:  358
year:  1783.0
log_CO2_277_3:  0.007716025
volcanic:  0.00811969
temperature_C:  8.1248951
fit:  8.3764448
------------
id:  359
year:  1783.0833329999998
log_CO2_277_3:  0.007785435
volcanic:  7.643861586
temperature_C:  8.1405258
fit:  8.2611027
------------
id:  360
year:  1783.1666670000002
log_CO2_277_3:  0.007854948
volcanic:  15.06222873
temperature_C:  8.126683199999999
fit:  8.149053599999998
------------
id:  361
year:  1783.25
log_CO2_277_3:  0.007924562
volcanic:  22.26940937
temperature_C:  8.0815763
fit:  8.040204
------------
id:  362
year:  1783.3333329999998
log_CO2_277_3:  0.007994275
volcanic:  29.27141556
temperature_C:  8.1014471
fit:  7.9344625
------------
id:  363
year:  1783.4166670000002
log_CO2_277_3:  0.008064084000000001
volcanic:  36.07408822
temperature_C:  8.0012484
fit:  7.8317409
------------
id:  364
year

volcanic:  5.511873857
temperature_C:  8.335500699999999
fit:  8.32586
------------
id:  463
year:  1791.75
log_CO2_277_3:  0.015121906999999999
volcanic:  5.354961507
temperature_C:  8.244004200000001
fit:  8.3285379
------------
id:  464
year:  1791.8333329999998
log_CO2_277_3:  0.01518919
volcanic:  5.202516148
temperature_C:  8.165461500000001
fit:  8.3311481
------------
id:  465
year:  1791.9166670000002
log_CO2_277_3:  0.015256327
volcanic:  5.054410612
temperature_C:  8.229992900000001
fit:  8.3336906
------------
id:  466
year:  1792.0
log_CO2_277_3:  0.015323318
volcanic:  4.910521354
temperature_C:  8.286412200000001
fit:  8.336169199999999
------------
id:  467
year:  1792.0833329999998
log_CO2_277_3:  0.015390158000000001
volcanic:  4.770728343
temperature_C:  8.343914999999999
fit:  8.3385849
------------
id:  468
year:  1792.1666670000002
log_CO2_277_3:  0.015456846000000002
volcanic:  4.634914968
temperature_C:  8.2221003
fit:  8.340939500000001
------------
id:  469
ye

...

id:  2591
year:  1969.0833329999998
log_CO2_277_3:  0.155589117
volcanic:  3.0300363
temperature_C:  8.7240496
fit:  8.9911299
------------
id:  2592
year:  1969.1666670000002
log_CO2_277_3:  0.156010889
volcanic:  2.943777049
temperature_C:  8.7378635
fit:  8.9943199
------------
id:  2593
year:  1969.25
log_CO2_277_3:  0.156517294
volcanic:  2.85997343
temperature_C:  8.7714367
fit:  8.997851400000002
------------
id:  2594
year:  1969.3333329999998
log_CO2_277_3:  0.156910417
volcanic:  2.778555538
temperature_C:  8.775355300000001
fit:  9.000840199999999
------------
id:  2595
year:  1969.4166670000002
log_CO2_277_3:  0.157305953
volcanic:  2.6994554560000004
temperature_C:  8.8128977
fit:  9.0038052
------------
id:  2596
year:  1969.5
log_CO2_277_3:  0.157632024
volcanic:  2.622607199
temperature_C:  8.880409199999999
fit:  9.0064249
------------
id:  2597
year:  1969.5833329999998
log_CO2_277_3:  0.157896397
volcanic:  2.5479466630000003
temperature_C:  8.936940199999999
fit:  9

fit:  9.1466532
------------
id:  2702
year:  1978.3333329999998
log_CO2_277_3:  0.189624163
volcanic:  2.633092966
temperature_C:  9.003588699999998
fit:  9.1491556
------------
id:  2703
year:  1978.4166670000002
log_CO2_277_3:  0.189974662
volcanic:  2.55813392
temperature_C:  8.983976400000001
fit:  9.1518555
------------
id:  2704
year:  1978.5
log_CO2_277_3:  0.19031261600000002
volcanic:  2.485308813
temperature_C:  8.985886599999999
fit:  9.1544685
------------
id:  2705
year:  1978.5833329999998
log_CO2_277_3:  0.190588361
volcanic:  2.414556896
temperature_C:  8.9878836
fit:  9.156771699999998
------------
id:  2706
year:  1978.6666670000002
log_CO2_277_3:  0.190933557
volcanic:  2.345819148
temperature_C:  8.950434699999999
fit:  9.1593542
------------
id:  2707
year:  1978.75
log_CO2_277_3:  0.1913109
volcanic:  2.27903823
temperature_C:  8.9305811
fit:  9.162051199999999
------------
id:  2708
year:  1978.8333329999998
log_CO2_277_3:  0.19160374
volcanic:  2.214158436
temp

------------
id:  2820
year:  1988.1666670000002
log_CO2_277_3:  0.235123167
volcanic:  2.061262583
temperature_C:  9.4627304
fit:  9.361031500000001
------------
id:  2821
year:  1988.25
log_CO2_277_3:  0.23571928
volcanic:  2.002582439
temperature_C:  9.4796648
fit:  9.364583
------------
id:  2822
year:  1988.3333329999998
log_CO2_277_3:  0.23629605399999998
volcanic:  1.945572804
temperature_C:  9.510564800000001
fit:  9.368022900000001
------------
id:  2823
year:  1988.4166670000002
log_CO2_277_3:  0.23681795
volcanic:  1.890186123
temperature_C:  9.5187263
fit:  9.371192
------------
id:  2824
year:  1988.5
log_CO2_277_3:  0.237353796
volcanic:  1.8363761930000002
temperature_C:  9.4986925
fit:  9.374400099999999
------------
id:  2825
year:  1988.5833329999998
log_CO2_277_3:  0.23794858100000002
volcanic:  1.7840981280000001
temperature_C:  9.4387188
fit:  9.377848599999998
------------
id:  2826
year:  1988.6666670000002
log_CO2_277_3:  0.23831807
volcanic:  1.7333083169999999

fit:  9.491458900000001
------------
id:  2932
year:  1997.5
log_CO2_277_3:  0.27130702
volcanic:  3.861630525
temperature_C:  9.492846499999999
fit:  9.4953728
------------
id:  2933
year:  1997.5833329999998
log_CO2_277_3:  0.271797224
volcanic:  3.7516974000000003
temperature_C:  9.5094595
fit:  9.4992275
------------
id:  2934
year:  1997.6666670000002
log_CO2_277_3:  0.272229962
volcanic:  3.644893858
temperature_C:  9.600462
fit:  9.5027781
------------
id:  2935
year:  1997.75
log_CO2_277_3:  0.272838683
volcanic:  3.541130805
temperature_C:  9.601472900000001
fit:  9.5070686
------------
id:  2936
year:  1997.8333329999998
log_CO2_277_3:  0.27337844
volcanic:  3.440321685
temperature_C:  9.6525631
fit:  9.5110064
------------
id:  2937
year:  1997.9166670000002
log_CO2_277_3:  0.27401845399999997
volcanic:  3.342382404
temperature_C:  9.703949900000001
fit:  9.515348399999999
------------
id:  2938
year:  1998.0
log_CO2_277_3:  0.274785929
volcanic:  3.247231265
temperature_C: 

id:  3047
year:  2007.0833329999998
log_CO2_277_3:  0.322850944
volcanic:  0.139423289
temperature_C:  10.007511099999999
fit:  9.781965300000001
------------
id:  3048
year:  2007.1666670000002
log_CO2_277_3:  0.323188187
volcanic:  0.135454178
temperature_C:  9.9887867
fit:  9.783531199999999
------------
id:  3049
year:  2007.25
log_CO2_277_3:  0.323618822
volcanic:  0.131598061
temperature_C:  9.995314599999999
fit:  9.7855129
------------
id:  3050
year:  2007.3333329999998
log_CO2_277_3:  0.324049272
volcanic:  0.12785172
temperature_C:  9.996296899999999
fit:  9.7874918
------------
id:  3051
year:  2007.4166670000002
log_CO2_277_3:  0.324536022
volcanic:  0.124212029
temperature_C:  10.0030127
fit:  9.7897205
------------
id:  3052
year:  2007.5
log_CO2_277_3:  0.32499213600000004
volcanic:  0.120675954
temperature_C:  9.9616404
fit:  9.7918119
------------
id:  3053
year:  2007.5833329999998
log_CO2_277_3:  0.325537027
volcanic:  0.117240544
temperature_C:  9.8260422
fit:  9.7

In [19]:
items = session.query(Eruptions)
for item in items:
    print("-"*12)
    print("id: ", item.id)
    print('volcano_name',item.volcano_name)
    print('vei',item.vei)
    print('start_year',item.start_year)
    print('start_month',item.start_month)
    print('start_day',item.start_day)
    print('end_year',item.end_year)
    print('end_month',item.end_month)
    print('end_day',item.end_day)
    print('country',item.country)
    print('region',item.region)
    print('latitude',item.latitude)
    print('longitude',item.longitude)
    print('elevation',item.elevation)
    print('primary_volcano_type',item.primary_volcano_type)
    print('status',item.status)

------------
id:  1
volcano_name Erebus
vei 2
start_year 1972
start_month 12
start_day 16
end_year 2018
end_month 2
end_day 7
country Antarctica
region Antarctica
latitude -77.53
longitude 167.17
elevation 3794.0
primary_volcano_type Stratovolcano
status Historical
------------
id:  2
volcano_name Erebus
vei 1
start_year 1972
start_month 1
start_day 3
end_year None
end_month None
end_day None
country Antarctica
region Antarctica
latitude -77.53
longitude 167.17
elevation 3794.0
primary_volcano_type Stratovolcano
status Historical
------------
id:  3
volcano_name Erebus
vei 0
start_year 1963
start_month 11
start_day 16
end_year None
end_month None
end_day None
country Antarctica
region Antarctica
latitude -77.53
longitude 167.17
elevation 3794.0
primary_volcano_type Stratovolcano
status Historical
------------
id:  4
volcano_name Erebus
vei 2
start_year 1955
start_month 7
start_day 2
end_year None
end_month None
end_day None
country Antarctica
region Antarctica
latitude -77.53
longitude

start_day 0
end_year None
end_month None
end_day None
country Antarctica
region Antarctica
latitude -62.1
longitude -57.93
elevation 180.0
primary_volcano_type Stratovolcano
status Lichenometry
------------
id:  56
volcano_name Penguin Island
vei None
start_year 1683
start_month 0
start_day 0
end_year None
end_month None
end_day None
country Antarctica
region Antarctica
latitude -62.1
longitude -57.93
elevation 180.0
primary_volcano_type Stratovolcano
status Lichenometry
------------
id:  57
volcano_name Southern Thule
vei 1
start_year 1975
start_month 7
start_day 2
end_year None
end_month None
end_day None
country United Kingdom
region Antarctica
latitude -59.442
longitude -27.225
elevation 1075.0
primary_volcano_type Stratovolcano(es)
status None
------------
id:  58
volcano_name Bristol Island
vei 1
start_year 2016
start_month 4
start_day 24
end_year 2016
end_month 7
end_day 19
country United Kingdom
region Antarctica
latitude -59.017
longitude -26.533
elevation 1100.0
primary_volca

id:  103
volcano_name McDonald Islands
vei 1
start_year 1996
start_month 12
start_day 16
end_year 1997
end_month 2
end_day 10
country Australia
region Middle East and Indian Ocean
latitude -53.03
longitude 72.6
elevation 230.0
primary_volcano_type Complex
status Historical
------------
id:  104
volcano_name McDonald Islands
vei 0
start_year 1992
start_month 12
start_day 16
end_year None
end_month None
end_day None
country Australia
region Middle East and Indian Ocean
latitude -53.03
longitude 72.6
elevation 230.0
primary_volcano_type Complex
status Historical
------------
id:  105
volcano_name Burney, Monte
vei 2
start_year 1910
start_month 3
start_day 0
end_year None
end_month None
end_day None
country Chile
region South America
latitude -52.33
longitude -73.4
elevation 1758.0
primary_volcano_type Stratovolcano
status Historical
------------
id:  106
volcano_name Burney, Monte
vei None
start_year -90
start_month 0
start_day 0
end_year None
end_month None
end_day None
country Chile
reg

country Chile
region South America
latitude -45.1
longitude -73.17
elevation 2960.0
primary_volcano_type Stratovolcano
status None
------------
id:  148
volcano_name Maca
vei None
start_year 410
start_month 0
start_day 0
end_year None
end_month None
end_day None
country Chile
region South America
latitude -45.1
longitude -73.17
elevation 2960.0
primary_volcano_type Stratovolcano
status None
------------
id:  149
volcano_name Mentolat
vei None
start_year 1710
start_month 0
start_day 0
end_year None
end_month None
end_day None
country Chile
region South America
latitude -44.7
longitude -73.08
elevation 1660.0
primary_volcano_type Stratovolcano
status None
------------
id:  150
volcano_name Mentolat
vei None
start_year -5010
start_month 0
start_day 0
end_year None
end_month None
end_day None
country Chile
region South America
latitude -44.7
longitude -73.08
elevation 1660.0
primary_volcano_type Stratovolcano
status None
------------
id:  151
volcano_name Melimoyu
vei None
start_year 200
s

start_month 4
start_day 0
end_year 1917
end_month 5
end_day 0
country Chile
region South America
latitude -41.33
longitude -72.618
elevation 1974.0
primary_volcano_type Stratovolcano
status None
------------
id:  188
volcano_name Calbuco
vei 2
start_year 1911
start_month 0
start_day 0
end_year 1912
end_month 0
end_day 0
country Chile
region South America
latitude -41.33
longitude -72.618
elevation 1974.0
primary_volcano_type Stratovolcano
status None
------------
id:  189
volcano_name Calbuco
vei 2
start_year 1909
start_month 3
start_day 0
end_year None
end_month None
end_day None
country Chile
region South America
latitude -41.33
longitude -72.618
elevation 1974.0
primary_volcano_type Stratovolcano
status None
------------
id:  190
volcano_name Calbuco
vei 2
start_year 1907
start_month 4
start_day 22
end_year None
end_month None
end_day None
country Chile
region South America
latitude -41.33
longitude -72.618
elevation 1974.0
primary_volcano_type Stratovolcano
status None
------------

...

start_month 5
start_day 0
end_year None
end_month None
end_day None
country Iceland
region Iceland and Arctic Ocean
latitude 64.416
longitude -17.316
elevation 1719.0
primary_volcano_type Caldera
status None
------------
id:  9629
volcano_name Grimsvotn
vei None
start_year 1934
start_month 12
start_day 21
end_year 1934
end_month 12
end_day 26
country Iceland
region Iceland and Arctic Ocean
latitude 64.416
longitude -17.316
elevation 1719.0
primary_volcano_type Caldera
status None
------------
id:  9630
volcano_name Grimsvotn
vei 2
start_year 1934
start_month 3
start_day 30
end_year 1934
end_month 4
end_day 7
country Iceland
region Iceland and Arctic Ocean
latitude 64.416
longitude -17.316
elevation 1719.0
primary_volcano_type Caldera
status None
------------
id:  9631
volcano_name Grimsvotn
vei 1
start_year 1933
start_month 11
start_day 29
end_year 1933
end_month 12
end_day 9
country Iceland
region Iceland and Arctic Ocean
latitude 64.416
longitude -17.316
elevation 1719.0
primary_volc

end_year None
end_month None
end_day None
country Iceland
region Iceland and Arctic Ocean
latitude 64.416
longitude -17.316
elevation 1719.0
primary_volcano_type Caldera
status None
------------
id:  9674
volcano_name Grimsvotn
vei None
start_year 1470
start_month 0
start_day 0
end_year None
end_month None
end_day None
country Iceland
region Iceland and Arctic Ocean
latitude 64.416
longitude -17.316
elevation 1719.0
primary_volcano_type Caldera
status None
------------
id:  9675
volcano_name Grimsvotn
vei None
start_year 1469
start_month 0
start_day 0
end_year None
end_month None
end_day None
country Iceland
region Iceland and Arctic Ocean
latitude 64.416
longitude -17.316
elevation 1719.0
primary_volcano_type Caldera
status None
------------
id:  9676
volcano_name Grimsvotn
vei None
start_year 1450
start_month 0
start_day 0
end_year None
end_month None
end_day None
country Iceland
region Iceland and Arctic Ocean
latitude 64.416
longitude -17.316
elevation 1719.0
primary_volcano_type C

latitude 64.633
longitude -17.516
elevation 2000.0
primary_volcano_type Stratovolcano
status None
------------
id:  9718
volcano_name Bardarbunga
vei 3
start_year 1717
start_month 8
start_day 4
end_year 1717
end_month 9
end_day 17
country Iceland
region Iceland and Arctic Ocean
latitude 64.633
longitude -17.516
elevation 2000.0
primary_volcano_type Stratovolcano
status None
------------
id:  9719
volcano_name Bardarbunga
vei 2
start_year 1716
start_month 10
start_day 5
end_year None
end_month None
end_day None
country Iceland
region Iceland and Arctic Ocean
latitude 64.633
longitude -17.516
elevation 2000.0
primary_volcano_type Stratovolcano
status None
------------
id:  9720
volcano_name Bardarbunga
vei 2
start_year 1712
start_month 1
start_day 15
end_year None
end_month None
end_day None
country Iceland
region Iceland and Arctic Ocean
latitude 64.633
longitude -17.516
elevation 2000.0
primary_volcano_type Stratovolcano
status None
------------
id:  9721
volcano_name Bardarbunga
vei 2

end_year None
end_month None
end_day None
country Iceland
region Iceland and Arctic Ocean
latitude 64.8
longitude -23.783
elevation 1446.0
primary_volcano_type Stratovolcano
status None
------------
id:  9765
volcano_name Snaefellsjokull
vei None
start_year -8460
start_month 0
start_day 0
end_year None
end_month None
end_day None
country Iceland
region Iceland and Arctic Ocean
latitude 64.8
longitude -23.783
elevation 1446.0
primary_volcano_type Stratovolcano
status None
------------
id:  9766
volcano_name Langjokull
vei 2
start_year 950
start_month 0
start_day 0
end_year None
end_month None
end_day None
country Iceland
region Iceland and Arctic Ocean
latitude 64.85
longitude -19.7
elevation 1100.0
primary_volcano_type Subglacial
status None
------------
id:  9767
volcano_name Langjokull
vei 0
start_year -2050
start_month 0
start_day 0
end_year None
end_month None
end_day None
country Iceland
region Iceland and Arctic Ocean
latitude 64.85
longitude -19.7
elevation 1100.0
primary_volcan

vei 0
start_year 850
start_month 0
start_day 0
end_year None
end_month None
end_day None
country Iceland
region Iceland and Arctic Ocean
latitude 65.715
longitude -16.728
elevation 800.0
primary_volcano_type Caldera
status None
------------
id:  9810
volcano_name Krafla
vei 0
start_year 250
start_month 0
start_day 0
end_year None
end_month None
end_day None
country Iceland
region Iceland and Arctic Ocean
latitude 65.715
longitude -16.728
elevation 800.0
primary_volcano_type Caldera
status None
------------
id:  9811
volcano_name Krafla
vei 2
start_year -50
start_month 0
start_day 0
end_year None
end_month None
end_day None
country Iceland
region Iceland and Arctic Ocean
latitude 65.715
longitude -16.728
elevation 800.0
primary_volcano_type Caldera
status None
------------
id:  9812
volcano_name Krafla
vei 2
start_year -300
start_month 0
start_day 0
end_year None
end_month None
end_day None
country Iceland
region Iceland and Arctic Ocean
latitude 65.715
longitude -16.728
elevation 800.0

In [20]:
items = session.query(Risk)
for item in items:
    print("-"*12)
    print('id', item.id)
    print('city', item.city)
    print('lat', item.lat)
    print('lng', item.lng)
    print('pop', item.pop)
    print('country', item.country)
    print('time', item.time)
    print('dist', item.dist)
    print('risk', item.risk)

------------
id 1
city Qal eh-ye Now
lat 34.98300013
lng 63.13329964
pop 2997.0
country Afghanistan
time 130.0
dist 102.39031704503824
risk 4.169192476657067
------------
id 2
city Chaghcharan
lat 34.5167011
lng 65.25000063
pop 15000.0
country Afghanistan
time 730.0
dist 875.5940273199917
risk 0.8420204946462038
------------
id 3
city Lashkar Gah
lat 31.58299802
lng 64.35999955
pop 201546.0
country Afghanistan
time 77.0
dist 694.0080079065492
risk 1.6895443290478551
------------
id 4
city Zaranj
lat 31.11200108
lng 61.88699752
pop 49851.0
country Afghanistan
time 226.0
dist 161.68149638368016
risk 3.6332941054335897
------------
id 5
city Tarin Kowt
lat 32.63329815
lng 65.86669865
pop 10000.0
country Afghanistan
time 7850.0
dist 141.59776930516026
risk 3.3284932997318277
------------
id 6
city Zareh Sharan
lat 32.85000016
lng 68.41670453
pop 13737.0
country Afghanistan
time 87.0
dist 197.62167808192783
risk 3.379623904229868
------------
id 7
city Asadabad
lat 34.86600004
lng 71.150004

pop 134855.0
country Algeria
time 16.0
dist 666.0737426838367
risk 2.0406381980918966
------------
id 82
city Tiarat
lat 35.38043601
lng 1.319960489
pop 184195.0
country Algeria
time 10.0
dist 385.1484217113564
risk 3.0051126640178234
------------
id 83
city Bejaia
lat 36.76037762
lng 5.070015827
pop 274520.0
country Algeria
time 157.0
dist 219.5968483154822
risk 3.3361813464285275
------------
id 84
city Blida
lat 36.4203467
lng 2.829997517
pop 388174.0
country Algeria
time 4.0
dist 268.88397837299823
risk 3.8422649930703816
------------
id 85
city Bouira
lat 36.38047833
lng 3.900009724
pop 110144.0
country Algeria
time 389.0
dist 212.1027063021363
risk 3.2066716299867983
------------
id 86
city Medea
lat 36.27040753
lng 2.770001179
pop 145863.5
country Algeria
time 1173.0
dist 147.63206535250222
risk 3.6410604189612985
------------
id 87
city Souk Ahras
lat 36.29038047
lng 7.949995075
pop 134947.0
country Algeria
time 1580.0
dist 424.858188216874
risk 2.01052731581818
------------
id

country Argentina
time 6.0
dist 75.03180296269527
risk 5.529446512040118
------------
id 159
city San Martin
lat -33.06998533
lng -68.49001612
pop 99974.0
country Argentina
time 17.0
dist 39.4608130612354
risk 6.23429935304549
------------
id 160
city Uspallata
lat -32.59311522
lng -69.34598454
pop 2390.0
country Argentina
time 380.0
dist 471.67084972366587
risk 1.6976721094100031
------------
id 161
city Cutral Co
lat -38.94001463
lng -69.24002202
pop 47597.0
country Argentina
time 470.0
dist 507.4461854431238
risk 1.8076918880462656
------------
id 162
city Punta Alta
lat -38.87996662
lng -62.0799681
pop 55969.5
country Argentina
time 1460.0
dist 145.76467766603318
risk 3.5731452626083877
------------
id 163
city San Nicolas
lat -33.33002114
lng -60.24000289
pop 117123.5
country Argentina
time 20.0
dist 314.64747388257706
risk 3.115905981731933
------------
id 164
city Campana
lat -34.15999632
lng -58.95997766
pop 77149.5
country Argentina
time 7.0
dist 652.8032548205819
risk 2.24281

pop 55249.0
country Argentina
time 20.0
dist 290.6334428655636
risk 3.1852484058695634
------------
id 239
city Libertador General San Martin
lat -23.81954222
lng -64.78998356
pop 47559.0
country Argentina
time 6.0
dist 288.59222392459
risk 3.4868126011684257
------------
id 240
city Chilecito
lat -29.16552081
lng -67.49999903
pop 20343.0
country Argentina
time 9570.0
dist 185.9431544833756
risk 2.9590716804491137
------------
id 241
city Chamical
lat -30.34958291
lng -66.31666039999999
pop 8989.0
country Argentina
time 86.0
dist 480.9683320081639
risk 2.003264616719179
------------
id 242
city Los Blancos
lat -23.59960732
lng -62.60003972
pop 1145.0
country Argentina
time 100.0
dist 127.04970189234292
risk 3.7906951635278636
------------
id 243
city Cafayate
lat -26.08291828
lng -65.96660425
pop 9478.0
country Argentina
time 3.0
dist 381.5402089310582
risk 3.1362217990106402
------------
id 244
city Cerrillos
lat -24.89963133
lng -65.48330042
pop 11498.0
country Argentina
time 7570.0


country Australia
time 1460.0
dist 318.82989861713884
risk 2.273646567215081
------------
id 317
city Tom Price
lat -22.69346108
lng 117.7930578
pop 1822.0
country Australia
time 7200.0
dist 381.9090396843763
risk 1.6849948739455485
------------
id 318
city Kalbarri
lat -27.66618081
lng 114.1666642
pop 1537.0
country Australia
time 13.0
dist 500.5896222880514
risk 2.1611452097457096
------------
id 319
city Port Denison
lat -29.28282632
lng 114.9166442
pop 1213.0
country Australia
time 14.0
dist 218.83645962462663
risk 3.3689655534989416
------------
id 320
city Merredin
lat -31.48284707
lng 118.2666723
pop 2054.0
country Australia
time 4.0
dist 780.8600061528333
risk 1.8306598198967172
------------
id 321
city Mount Barker
lat -34.632784
lng 117.66660559999998
pop 1771.5
country Australia
time 220.0
dist 341.7142656120798
risk 2.228365130955825
------------
id 322
city Katanning
lat -33.69955931
lng 117.5500752
pop 3140.0
country Australia
time 5070.0
dist 325.1990686941745
risk 2.011

...

pop 102151.5
country United States of America
time 5370.0
dist 368.99750000577257
risk 2.0889387832625066
------------
id 6555
city Great Falls
lat 47.50029055
lng -111.29998700000002
pop 61316.5
country United States of America
time 153.0
dist 471.36251559390837
risk 2.088786661643039
------------
id 6556
city Missoula
lat 46.87224103
lng -113.99305259999998
pop 68010.0
country United States of America
time 61.0
dist 595.072686940288
risk 1.8923248761598852
------------
id 6557
city Minot
lat 48.23249392
lng -101.2958173
pop 37162.0
country United States of America
time 6920.0
dist 148.7075318754903
risk 3.3670681408784637
------------
id 6558
city Fargo
lat 46.8772278
lng -96.7894257
pop 127472.5
country United States of America
time 9070.0
dist 425.8615094990837
risk 1.8414975383117045
------------
id 6559
city Hilo
lat 19.69999778
lng -155.0900273
pop 47720.5
country United States of America
time 99.0
dist 208.21229693001519
risk 3.3732719378956864
------------
id 6560
city Olympia

time 6470.0
dist 73.50020656508842
risk 4.611472220159413
------------
id 6623
city Memphis
lat 35.11998679999999
lng -89.99999516
pop 753843.5
country United States of America
time 5.0
dist 359.6203110524943
risk 3.3783846213079762
------------
id 6624
city Norfolk
lat 36.84995872
lng -76.28000574
pop 645336.0
country United States of America
time 97.0
dist 785.9352385612706
risk 1.5317954038592199
------------
id 6625
city Milwaukee
lat 43.05265505
lng -87.91996708
pop 983590.0
country United States of America
time 13.0
dist 499.4860076271925
risk 2.6446070901623444
------------
id 6626
city Buffalo
lat 42.87997825
lng -78.88000208
pop 647778.5
country United States of America
time 110.0
dist 641.1753548003321
risk 1.8205811877087577
------------
id 6627
city Pittsburgh
lat 40.42999860000001
lng -79.99998539
pop 1535267.5
country United States of America
time 64.0
dist 460.04065645700615
risk 2.4615140086027463
------------
id 6628
city Kodiak
lat 57.78999839
lng -152.4069869
pop 780

city Denow
lat 38.27715843
lng 67.88716345
pop 143134.0
country Uzbekistan
time 200.0
dist 511.5332922561132
risk 1.9823297971157945
------------
id 6695
city Guliston
lat 40.49573102
lng 68.79072587
pop 74446.5
country Uzbekistan
time 105.0
dist 371.9430298283543
risk 2.5186265796810723
------------
id 6696
city Iskandar
lat 41.55073122
lng 69.68074906
pop 111634.5
country Uzbekistan
time 32.0
dist 548.1776269367778
risk 2.1724195854814767
------------
id 6697
city Chirchiq
lat 41.45497479
lng 69.55998124
pop 155093.5
country Uzbekistan
time 10.0
dist 445.38010225742926
risk 2.7743427569561296
------------
id 6698
city Kogon
lat 39.72107546
lng 64.54576534
pop 85093.0
country Uzbekistan
time 7070.0
dist 223.3406156293187
risk 2.8110772693705157
------------
id 6699
city Khiwa
lat 41.39112856
lng 60.35573686
pop 102659.0
country Uzbekistan
time 5270.0
dist 445.6526838280468
risk 1.805292125914452
------------
id 6700
city Chimboy
lat 42.93113792
lng 59.77075964
pop 34277.5
country Uzbe

city San Cristobal
lat 7.770002461
lng -72.24996749
pop 342690.5
country Venezuela
time 165.0
dist 63.62777157126681
risk 5.19279470217389
------------
id 6767
city Valencia
lat 10.22998151
lng -67.9800214
pop 1569526.5
country Venezuela
time 29.0
dist 19.896269591750304
risk 7.251336978473495
------------
id 6768
city Ciudad Guayana
lat 8.370017516
lng -62.61998682
pop 634317.5
country Venezuela
time 7.0
dist 160.2828084744
risk 4.494801330527467
------------
id 6769
city Maracaibo
lat 10.72997683
lng -71.65997766
pop 1764650.0
country Venezuela
time 2770.0
dist 200.50202538465888
risk 3.2385146390649586
------------
id 6770
city Caracas
lat 10.50099855
lng -66.91703719
pop 2400339.5
country Venezuela
time 764.0
dist 359.06686565635454
risk 2.509723231204893
------------
id 6771
city Tay Ninh
lat 11.32299911
lng 106.1469997
pop 126370.0
country Vietnam
time 20.0
dist 146.3527911859351
risk 4.273898564113063
------------
id 6772
city Luan Chau
lat 21.74000399
lng 103.3430047
pop 7335.0

id 6844
city Sadah
lat 16.93977867
lng 43.84976762
pop 105542.0
country Yemen
time 3.0
dist 383.12788115961774
risk 3.3075938488096663
------------
id 6845
city Al Hudaydah
lat 14.79794558
lng 42.95297481
pop 627610.5
country Yemen
time 32.0
dist 28.373055003666515
risk 6.6829940802985
------------
id 6846
city Al Mukalla
lat 14.54116538
lng 49.12593135
pop 194080.5
country Yemen
time 46.0
dist 301.84978466156485
risk 3.0397276995458884
------------
id 6847
city Taizz
lat 13.60445253
lng 44.03942012
pop 683111.0
country Yemen
time 5870.0
dist 537.1088177868634
risk 1.6287076414755153
------------
id 6848
city Aden
lat 12.77972251
lng 45.00949011
pop 775301.0
country Yemen
time 13.0
dist 425.36043954723283
risk 2.874627495340984
------------
id 6849
city Sanaa
lat 15.3547333
lng 44.20659338
pop 1921926.5
country Yemen
time 1370.0
dist 410.4451299529861
risk 2.231837871954706
------------
id 6850
city Kawambwa
lat -9.779520651
lng 29.08002315
pop 20355.0
country Zambia
time 126.0
dist 59

In [21]:
items = session.query(WorldCities)
for item in items:
    print("-"*12)
    print('id: ', item.id)
    print('city: ', item.city)
    print('city_ascii: ', item.city_ascii)
    print('lat: ', item.lat)
    print('lng: ', item.lng)
    print('pop: ', item.pop)
    print('country: ', item.country)
    print('iso2: ', item.iso2)
    print('iso3: ', item.iso3)
    print('province: ', item.province)

------------
id:  1
city:  Qal eh-ye Now
city_ascii:  Qal eh-ye
lat:  34.98300013
lng:  63.13329964
pop:  2997.0
country:  Afghanistan
iso2:  AF
iso3:  AFG
province:  Badghis
------------
id:  2
city:  Chaghcharan
city_ascii:  Chaghcharan
lat:  34.5167011
lng:  65.25000063
pop:  15000.0
country:  Afghanistan
iso2:  AF
iso3:  AFG
province:  Ghor
------------
id:  3
city:  Lashkar Gah
city_ascii:  Lashkar Gah
lat:  31.58299802
lng:  64.35999955
pop:  201546.0
country:  Afghanistan
iso2:  AF
iso3:  AFG
province:  Hilmand
------------
id:  4
city:  Zaranj
city_ascii:  Zaranj
lat:  31.11200108
lng:  61.88699752
pop:  49851.0
country:  Afghanistan
iso2:  AF
iso3:  AFG
province:  Nimroz
------------
id:  5
city:  Tarin Kowt
city_ascii:  Tarin Kowt
lat:  32.63329815
lng:  65.86669865
pop:  10000.0
country:  Afghanistan
iso2:  AF
iso3:  AFG
province:  Uruzgan
------------
id:  6
city:  Zareh Sharan
city_ascii:  Zareh Sharan
lat:  32.85000016
lng:  68.41670453
pop:  13737.0
country:  Afghanistan

iso3:  DZA
province:  Constantine
------------
id:  108
city:  Oran
city_ascii:  Oran
lat:  35.71000246
lng:  -0.61997278
pop:  721992.0
country:  Algeria
iso2:  DZ
iso3:  DZA
province:  Oran
------------
id:  109
city:  Tamanrasset
city_ascii:  Tamanrasset
lat:  22.78500327
lng:  5.5228047270000005
pop:  71808.0
country:  Algeria
iso2:  DZ
iso3:  DZA
province:  Tamanghasset
------------
id:  110
city:  Ghardaia
city_ascii:  Ghardaia
lat:  32.48999229
lng:  3.669997923
pop:  125480.0
country:  Algeria
iso2:  DZ
iso3:  DZA
province:  Ghardaïa
------------
id:  111
city:  Algiers
city_ascii:  Algiers
lat:  36.763064799999995
lng:  3.05055253
pop:  2665831.5
country:  Algeria
iso2:  DZ
iso3:  DZA
province:  Alger
------------
id:  112
city:  Pago Pago
city_ascii:  Pago Pago
lat:  -14.2766105
lng:  -170.70664509999997
pop:  12038.0
country:  American Samoa
iso2:  AS
iso3:  ASM
province:  None
------------
id:  113
city:  Andorra
city_ascii:  Andorra
lat:  42.50000144
lng:  1.51648596099999

province:  None
------------
id:  180
city:  Mirny Station
city_ascii:  Mirny Station
lat:  -66.57552952
lng:  93.00628846
pop:  114.5
country:  Antarctica
iso2:  AQ
iso3:  ATA
province:  None
------------
id:  181
city:  Mawson Station
city_ascii:  Mawson Station
lat:  -67.61452032
lng:  62.87500073
pop:  40.0
country:  Antarctica
iso2:  AQ
iso3:  ATA
province:  None
------------
id:  182
city:  Davis Station
city_ascii:  Davis Station
lat:  -68.77767439
lng:  78.14073509
pop:  45.0
country:  Antarctica
iso2:  AQ
iso3:  ATA
province:  None
------------
id:  183
city:  Concordia Research Station
city_ascii:  Concordia Research Station
lat:  -74.66630939
lng:  124.16703570000001
pop:  15.0
country:  Antarctica
iso2:  AQ
iso3:  ATA
province:  None
------------
id:  184
city:  Casey Station
city_ascii:  Casey Station
lat:  -66.28608614
lng:  110.53621399999999
pop:  125.0
country:  Antarctica
iso2:  AQ
iso3:  ATA
province:  None
------------
id:  185
city:  Amundsen–Scott South Pole Stati

lng:  -61.16658716
pop:  2921.0
country:  Argentina
iso2:  AR
iso3:  ARG
province:  Chaco
------------
id:  255
city:  Villa Angela
city_ascii:  Villa Angela
lat:  -27.58329181
lng:  -60.71666629999999
pop:  30051.0
country:  Argentina
iso2:  AR
iso3:  ARG
province:  Chaco
------------
id:  256
city:  Ingeniero Guillermo N. Juarez
city_ascii:  Ingeniero Guillermo N. Juarez
lat:  -23.90000242
lng:  -61.84998214
pop:  6453.0
country:  Argentina
iso2:  AR
iso3:  ARG
province:  Formosa
------------
id:  257
city:  Comandante Fontana
city_ascii:  Comandante Fontana
lat:  -25.33329995
lng:  -59.68331852
pop:  4277.0
country:  Argentina
iso2:  AR
iso3:  ARG
province:  Formosa
------------
id:  258
city:  Doctor Pedro P. Pena
city_ascii:  Doctor Pedro P. Pena
lat:  -22.47998574
lng:  -62.29998051
pop:  6143.0
country:  Argentina
iso2:  AR
iso3:  ARG
province:  Formosa
------------
id:  259
city:  San Lorenzo
city_ascii:  San Lorenzo
lat:  -28.12000324
lng:  -58.76998926
pop:  25833.5
country: 

province:  Córdoba
------------
id:  326
city:  San Salvador de Jujuy
city_ascii:  San Salvador de Jujuy
lat:  -24.1833443
lng:  -65.30002995
pop:  258739.0
country:  Argentina
iso2:  AR
iso3:  ARG
province:  Jujuy
------------
id:  327
city:  San Ramon de la Nueva Oran
city_ascii:  San Ramon de la Nueva Oran
lat:  -23.13999713
lng:  -64.32001225
pop:  69461.5
country:  Argentina
iso2:  AR
iso3:  ARG
province:  Salta
------------
id:  328
city:  Goya
city_ascii:  Goya
lat:  -29.13999266
lng:  -59.26998458
pop:  71274.5
country:  Argentina
iso2:  AR
iso3:  ARG
province:  Corrientes
------------
id:  329
city:  Puerto San Julian
city_ascii:  Puerto San Julian
lat:  -49.30000242
lng:  -67.71665247
pop:  2347.0
country:  Argentina
iso2:  AR
iso3:  ARG
province:  Santa Cruz
------------
id:  330
city:  Perito Moreno
city_ascii:  Perito Moreno
lat:  -46.60001219
lng:  -70.93335535
pop:  3766.0
country:  Argentina
iso2:  AR
iso3:  ARG
province:  Santa Cruz
------------
id:  331
city:  Rio Gra

...

city_ascii:  Augusta
lat:  44.31056276
lng:  -69.77998906
pop:  21301.0
country:  United States of America
iso2:  US
iso3:  USA
province:  Maine
------------
id:  7014
city:  Sault Ste. Marie
city_ascii:  Sault Ste. Marie
lat:  46.49526145
lng:  -84.34527572
pop:  50173.5
country:  United States of America
iso2:  US
iso3:  USA
province:  Michigan
------------
id:  7015
city:  Sitka
city_ascii:  Sitka
lat:  57.06039769
lng:  -135.32754939999998
pop:  8110.0
country:  United States of America
iso2:  US
iso3:  USA
province:  Alaska
------------
id:  7016
city:  Helena
city_ascii:  Helena
lat:  46.59274904
lng:  -112.03529099999999
pop:  33032.5
country:  United States of America
iso2:  US
iso3:  USA
province:  Montana
------------
id:  7017
city:  Bismarck
city_ascii:  Bismarck
lat:  46.80831728
lng:  -100.7833163
pop:  60288.5
country:  United States of America
iso2:  US
iso3:  USA
province:  North Dakota
------------
id:  7018
city:  Boise
city_ascii:  Boise
lat:  43.60859011
lng:  -116

city_ascii:  Santa Lucia
lat:  -34.47000324
lng:  -56.39997888
pop:  15264.5
country:  Uruguay
iso2:  UY
iso3:  URY
province:  Canelones
------------
id:  7087
city:  Jose Batlle y Ordonez
city_ascii:  Jose Batlle y Ordonez
lat:  -33.47001259
lng:  -55.12000533
pop:  2438.0
country:  Uruguay
iso2:  UY
iso3:  URY
province:  Lavalleja
------------
id:  7088
city:  Minas
city_ascii:  Minas
lat:  -34.37000934
lng:  -55.23002446
pop:  39602.5
country:  Uruguay
iso2:  UY
iso3:  URY
province:  Lavalleja
------------
id:  7089
city:  Maldonado
city_ascii:  Maldonado
lat:  -34.91002806
lng:  -54.95998926
pop:  51877.5
country:  Uruguay
iso2:  UY
iso3:  URY
province:  Maldonado
------------
id:  7090
city:  Punta del Este
city_ascii:  Punta del Este
lat:  -34.96997272
lng:  -54.94998987
pop:  84140.0
country:  Uruguay
iso2:  UY
iso3:  URY
province:  Maldonado
------------
id:  7091
city:  Aigua
city_ascii:  Aigua
lat:  -34.19999388
lng:  -54.75000208
pop:  2622.0
country:  Uruguay
iso2:  UY
iso3

iso2:  VE
iso3:  VEN
province:  Trujillo
------------
id:  7156
city:  Machiques
city_ascii:  Machiques
lat:  10.07043052
lng:  -72.54994918
pop:  44936.5
country:  Venezuela
iso2:  VE
iso3:  VEN
province:  Zulia
------------
id:  7157
city:  San Carlos del Zulia
city_ascii:  San Carlos del Zulia
lat:  9.010391865
lng:  -71.91998763
pop:  76935.0
country:  Venezuela
iso2:  VE
iso3:  VEN
province:  Zulia
------------
id:  7158
city:  Puerto Cabello
city_ascii:  Puerto Cabello
lat:  10.47043194
lng:  -68.17000981
pop:  174000.0
country:  Venezuela
iso2:  VE
iso3:  VEN
province:  Carabobo
------------
id:  7159
city:  Acarigua
city_ascii:  Acarigua
lat:  9.580382913
lng:  -69.20002446
pop:  202312.5
country:  Venezuela
iso2:  VE
iso3:  VEN
province:  Portuguesa
------------
id:  7160
city:  Upata
city_ascii:  Upata
lat:  8.020426452
lng:  -62.40999964
pop:  53474.5
country:  Venezuela
iso2:  VE
iso3:  VEN
province:  Bolívar
------------
id:  7161
city:  El Manteco
city_ascii:  El Manteco


iso2:  VN
iso3:  VNM
province:  Quảng Trị 
------------
id:  7221
city:  Vung Tau
city_ascii:  Vung Tau
lat:  10.35537437
lng:  107.08497759999999
pop:  229225.0
country:  Vietnam
iso2:  VN
iso3:  VNM
province:  Bà Rịa–Vũng Tàu 
------------
id:  7222
city:  Phan Thiet
city_ascii:  Phan Thiet
lat:  10.933736999999999
lng:  108.10005770000001
pop:  248749.0
country:  Vietnam
iso2:  VN
iso3:  VNM
province:  Bình Thuận 
------------
id:  7223
city:  Long Xuyen
city_ascii:  Long Xuyen
lat:  10.38038576
lng:  105.4200146
pop:  254076.5
country:  Vietnam
iso2:  VN
iso3:  VNM
province:  An Giang
------------
id:  7224
city:  Chau Doc
city_ascii:  Chau Doc
lat:  10.70039207
lng:  105.11667390000001
pop:  70239.0
country:  Vietnam
iso2:  VN
iso3:  VNM
province:  An Giang
------------
id:  7225
city:  Rach Gia
city_ascii:  Rach Gia
lat:  10.01539512
lng:  105.09135249999999
pop:  252830.0
country:  Vietnam
iso2:  VN
iso3:  VNM
province:  Kiên Giang
------------
id:  7226
city:  Tan An
city_ascii

country:  Zambia
iso2:  ZM
iso3:  ZMB
province:  North-Western
------------
id:  7282
city:  Solwezi
city_ascii:  Solwezi
lat:  -12.17958087
lng:  26.39998002
pop:  51793.5
country:  Zambia
iso2:  ZM
iso3:  ZMB
province:  North-Western
------------
id:  7283
city:  Choma
city_ascii:  Choma
lat:  -16.80947915
lng:  26.97002274
pop:  42324.0
country:  Zambia
iso2:  ZM
iso3:  ZMB
province:  Southern
------------
id:  7284
city:  Mongu
city_ascii:  Mongu
lat:  -15.27959837
lng:  23.12002519
pop:  45098.5
country:  Zambia
iso2:  ZM
iso3:  ZMB
province:  Western
------------
id:  7285
city:  Kaoma
city_ascii:  Kaoma
lat:  -14.77962889
lng:  24.79997432
pop:  7259.0
country:  Zambia
iso2:  ZM
iso3:  ZMB
province:  Western
------------
id:  7286
city:  Sesheke
city_ascii:  Sesheke
lat:  -17.46954222
lng:  24.30000484
pop:  10177.5
country:  Zambia
iso2:  ZM
iso3:  ZMB
province:  Western
------------
id:  7287
city:  Lukulu
city_ascii:  Lukulu
lat:  -14.38957518
lng:  23.24001786
pop:  3349.0
c

## Checking if database tables were updated properly

In [22]:
# Import SQLAlchemy `automap` and other dependencies
import sqlalchemy
from sqlalchemy.ext.automap import automap_base
from sqlalchemy.orm import Session
from sqlalchemy import create_engine, inspect
engine = create_engine("sqlite:///volcano_app/volcano.sqlite")

In [23]:
# Create the inspector and connect it to the engine
inspector = inspect(engine)
# Collect the names of tables within the database
inspector.get_table_names()

['berkeleydata', 'eruptions', 'risk', 'tempinfo', 'worldcities']

In [24]:
# conn = engine.connect()
# conn = engine.raw_connection()
# cursor = conn.cursor()
# command = "DROP TABLE IF EXISTS {};".format('risk')
# cursor.execute(command)
# conn.commit()
# cursor.close()

In [25]:
# Using the inspector to print the column names within the 'measurement' table and its types
columns = inspector.get_columns('eruptions')
for column in columns:
    print(column["name"], column["type"])

id INTEGER
volcano_name VARCHAR
vei INTEGER
start_year INTEGER
start_month INTEGER
start_day INTEGER
end_year INTEGER
end_month INTEGER
end_day INTEGER
country VARCHAR
region VARCHAR
latitude FLOAT
longitude FLOAT
elevation FLOAT
primary_volcano_type VARCHAR
status VARCHAR


In [26]:
# Using the inspector to print the column names within the 'measurement' table and its types
columns = inspector.get_columns('tempinfo')
for column in columns:
    print(column["name"], column["type"])

id INTEGER
year FLOAT
temp FLOAT
fit FLOAT


In [28]:
inspector.get_table_names()

['berkeleydata', 'eruptions', 'risk', 'tempinfo', 'worldcities']